In [1]:
import pygmt
import pandas as pd
import numpy as np
from obspy.clients.fdsn import Client
from obspy.core.utcdatetime import UTCDateTime
import datetime
from obspy.clients.fdsn import Client

## Load Station Information

In [2]:
# Obtain the station and network information 
all_picks_OR= pd.read_csv('/home/hbito/cascadia_obs_ensemble/data/datasets_OR/all_picks_OR.csv')
all_picks_OR = all_picks_OR.drop_duplicates(subset='station_code')
networks_stas=np.array(all_picks_OR[['station_network_code','station_code']])

available_stations = networks_stas
available_stations

## Load the event data

In [4]:
# Load the event data
mycatalog_picks = pd.read_csv('../data/datasets_OR/events_OR.csv')
mycatalog_picks

In [7]:
# Obtain the latitudes of longitude of the stations used
client = Client("IRIS")

sta_lat = []
sta_lon = []

for network, station in available_stations:

    # Fetch the station inventory
    inventory = client.get_stations(network=network, station=station, level='station')

    # The correct path to access the station's latitude and longitude
    _sta_lat = inventory[0][0].latitude
    _sta_lon = inventory[0][0].longitude
    
    sta_lat.append(_sta_lat)
    sta_lon.append(_sta_lon)
    

## Map the event

In [8]:
fig = pygmt.Figure()
# Load grid data
grid = pygmt.datasets.load_earth_relief(resolution="15s", region=[-127, -123, 40, 50])
shade = pygmt.grdgradient(grid=grid, azimuth="0/90", normalize="t1")
# Define target region
region = [-127, -123, 40, 50]
title = f"Oregon event: {mycatalog_picks['time']}"
fig.basemap(region=region, projection="M12c", frame=["af", f"WSne+t{title}"])
fig.grdimage(grid=grid, cmap="geo",shading=shade, transparency=50)

# Adjust plot calls to use 'style' correctly
# PLot the stations
fig.plot(x=sta_lon, y=sta_lat,  
         fill='black', style="t0.4c", pen="black", label="Stations")

# Plotting data points

fig.plot(x=mycatalog_picks['longitude'], y=mycatalog_picks['latitude'],  
         style="c0.3c", color='#e41a1c', pen="black", label=f"Event: depth=45.703125 km")

# Add a legend to the plot
fig.legend(position="JTR+w9+jTR", box='+gwhite+p1p')
fig.savefig("map_event_20160604.pdf")
# Display the figure
fig.show()



/tmp/ipykernel_3506413/680135319.py:18: FutureWarning: The 'color' parameter has been deprecated since v0.8.0 and will be removed in v0.12.0. Please use 'fill' instead.
  fig.plot(x=mycatalog_picks['longitude'], y=mycatalog_picks['latitude'],
